#### Introduction 

This version of the notebook is to be used only for hyperparameter tuning and experiments, assuming that the essential files (yaml, yolov5, folder structure) have already been setup.

In [1]:
import os
os.chdir("D:\\Datasets\\SIIM_RSNA_Covid_Datasets")
os.getcwd()

'D:\\Datasets\\SIIM_RSNA_Covid_Datasets'

In [2]:
import torch
print(f"Setup complete. Using torch {torch.__version__} ({torch.cuda.get_device_properties(0).name if torch.cuda.is_available() else 'CPU'})")

# Install W&B 
# !pip install -q --upgrade wandb
# Login 

import wandb
wandb.login()

# Necessary/extra dependencies. 
import os
import gc
import cv2
import numpy as np
import pandas as pd
from tqdm import tqdm
from shutil import copyfile
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split

#customize iPython writefile so we can write variables
from IPython.core.magic import register_line_cell_magic

@register_line_cell_magic
def writetemplate(line, cell):
    with open(line, 'w') as f:
        f.write(cell.format(**globals()))

Setup complete. Using torch 1.8.1 (NVIDIA GeForce GTX 1080 Ti)


wandb: Currently logged in as: ogk01 (use `wandb login --relogin` to force relogin)


### Hyperparameters

In [3]:
TRAIN_PATH = 'D:\\Datasets\\SIIM_RSNA_Covid_Datasets\\train_jpeg_512\\'
train_image_level_filepath = 'D:\\Datasets\\SIIM_RSNA_Covid_Datasets\\train_image_level.csv'
meta_filepath = 'D:\\Datasets\\SIIM_RSNA_Covid_Datasets\\meta_256.csv'
yolo_yaml_filepath = 'D:\\Datasets\\SIIM_RSNA_Covid_Datasets\\tmp\\yolov5\\data\\data.yaml'
IMG_SIZE = 512
BATCH_SIZE = 64
EPOCHS = 75

### Prepare Dataset

This is the most important section when it comes to training an object detector with YOLOv5. The directory structure, bounding box format, etc must be in the correct order. This section builds every piece needed to train a YOLOv5 model.

Using [xhlulu's](https://www.kaggle.com/xhlulu) resized dataset. The uploaded 256x256 Kaggle dataset is [here](https://www.kaggle.com/xhlulu/siim-covid19-resized-to-256px-jpg). Find other image resolutions [here](https://www.kaggle.com/c/siim-covid19-detection/discussion/239918).

* Create train-validation split. <br>
* Create required `/dataset` folder structure and more the images to that folder. <br>
* Create `data.yaml` file needed to train the model. <br>
* Create bounding box coordinates in the required YOLO format. 

In [4]:
# Everything is done from /kaggle directory.
#%cd ../

# Load image level csv file
df = pd.read_csv(train_image_level_filepath)

# Modify values in the id column
df['id'] = df.apply(lambda row: row.id.split('_')[0], axis=1)

# Add absolute path
df['path'] = df.apply(lambda row: TRAIN_PATH+row.id+'.jpg', axis=1)

# Get image level labels
df['image_level'] = df.apply(lambda row: row.label.split(' ')[0], axis=1)

df.head(5)

# Load meta.csv file
# Original dimensions are required to scale the bounding box coordinates appropriately.
meta_df = pd.read_csv(meta_filepath)
train_meta_df = meta_df.loc[meta_df.split == 'train']
train_meta_df = train_meta_df.drop('split', axis=1)
train_meta_df.columns = ['id', 'dim0', 'dim1']
train_meta_df.head(2)

# Merge both the dataframes
df = df.merge(train_meta_df, on='id',how="left")
df.head(2)

id                                              boxes  \
0  000a312787f2  [{'x': 789.28836, 'y': 582.43035, 'width': 102...   
1  000c3a3f293f                                                NaN   

                                               label StudyInstanceUID  \
0  opacity 1 789.28836 582.43035 1815.94498 2499....     5776db0cec75   
1                                     none 1 0 0 1 1     ff0879eb20ed   

                                                path image_level  dim0  dim1  
0  D:\Datasets\SIIM_RSNA_Covid_Datasets\train_jpe...     opacity  3488  4256  
1  D:\Datasets\SIIM_RSNA_Covid_Datasets\train_jpe...        none  2320  2832

## 🍘 Train-validation split

In [5]:
# Create train and validation split.
train_df, valid_df = train_test_split(df, test_size=0.2, random_state=42, stratify=df.image_level.values)

train_df.loc[:, 'split'] = 'train'
valid_df.loc[:, 'split'] = 'valid'

df = pd.concat([train_df, valid_df]).reset_index(drop=True)

print(f'Size of dataset: {len(df)}, training images: {len(train_df)}. validation images: {len(valid_df)}')

Size of dataset: 6334, training images: 5067. validation images: 1267


D:\Anaconda\envs\Pytorch\lib\site-packages\pandas\core\indexing.py:1597: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[key] = value
D:\Anaconda\envs\Pytorch\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)


## 🍚 Prepare Required Folder Structure

The required folder structure for the dataset directory is: 

```
/parent_folder
    /dataset
         /images
             /train
             /val
         /labels
             /train
             /val
    /yolov5
```

Note that I have named the directory `covid`.

In [7]:
# os.chdir("D:\\Datasets\\SIIM_RSNA_Covid_Datasets\\")
# os.makedirs('tmp/covid/images/train', exist_ok=True)
# os.makedirs('tmp/covid/images/valid', exist_ok=True)

# os.makedirs('tmp/covid/labels/train', exist_ok=True)
# os.makedirs('tmp/covid/labels/valid', exist_ok=True)

# #!ls tmp/covid/images

# # Move the images to relevant split folder.
# for i in tqdm(range(len(df))):
#     row = df.loc[i]
#     if row.split == 'train':
#         copyfile(row.path, f'D:\\Datasets\\SIIM_RSNA_Covid_Datasets\\tmp\\covid\\images\\train\\{row.id}.jpg')
#     else:
#         copyfile(row.path, f'D:\\Datasets\\SIIM_RSNA_Covid_Datasets\\tmp\\covid\\images\\valid\\{row.id}.jpg')

100%|█████████████████████████████████████████████████████████████████████████████| 6334/6334 [00:07<00:00, 828.51it/s]


#### Copy the images into the tmp folder created above

## 🍜 Create `.YAML` file

The `data.yaml`, is the dataset configuration file that defines 

1. an "optional" download command/URL for auto-downloading, 
2. a path to a directory of training images (or path to a *.txt file with a list of training images), 
3. a path to a directory of validation images (or path to a *.txt file with a list of validation images), 
4. the number of classes, 
5. a list of class names.

> 📍 Important: In this competition, each image can either belong to `opacity` or `none` image-level labels. That's why I have  used the number of classes, `nc` to be 2. YOLOv5 automatically handles the images without any bounding box coordinates. 

> 📍 Note: The `data.yaml` is created in the `yolov5/data` directory as required. 

In [8]:
# # Create .yaml file 
# import yaml

# data_yaml = dict(
#     train = '../covid/images/train',
#     val = '../covid/images/valid',
#     nc = 2,
#     names = ['none', 'opacity']
# )

# # Note that I am creating the file in the yolov5/data/ directory.
# with open(yolo_yaml_filepath, 'w') as outfile:
#     yaml.dump(data_yaml, outfile, default_flow_style=True)

## 🍮 Prepare Bounding Box Coordinated for YOLOv5

For every image with **bounding box(es)** a `.txt` file with the same name as the image will be created in the format shown below:

* One row per object. <br>
* Each row is class `x_center y_center width height format`. <br>
* Box coordinates must be in normalized xywh format (from 0 - 1). We can normalize by the boxes in pixels by dividing `x_center` and `width` by image width, and `y_center` and `height` by image height. <br>
* Class numbers are zero-indexed (start from 0). <br>

> 📍 Note: We don't have to remove the images without bounding boxes from the training or validation sets. 

In [6]:
# Get the raw bounding box by parsing the row value of the label column.
# Ref: https://www.kaggle.com/yujiariyasu/plot-3positive-classes
def get_bbox(row):
    bboxes = []
    bbox = []
    for i, l in enumerate(row.label.split(' ')):
        if (i % 6 == 0) | (i % 6 == 1):
            continue
        bbox.append(float(l))
        if i % 6 == 5:
            bboxes.append(bbox)
            bbox = []  
            
    return bboxes

# Scale the bounding boxes according to the size of the resized image. 
def scale_bbox(row, bboxes):
    # Get scaling factor
    scale_x = IMG_SIZE/row.dim1
    scale_y = IMG_SIZE/row.dim0
    
    scaled_bboxes = []
    for bbox in bboxes:
        x = int(np.round(bbox[0]*scale_x, 4))
        y = int(np.round(bbox[1]*scale_y, 4))
        x1 = int(np.round(bbox[2]*(scale_x), 4))
        y1= int(np.round(bbox[3]*scale_y, 4))

        scaled_bboxes.append([x, y, x1, y1]) # xmin, ymin, xmax, ymax
        
    return scaled_bboxes

# Convert the bounding boxes in YOLO format.
def get_yolo_format_bbox(img_w, img_h, bboxes):
    yolo_boxes = []
    for bbox in bboxes:
        w = bbox[2] - bbox[0] # xmax - xmin
        h = bbox[3] - bbox[1] # ymax - ymin
        xc = bbox[0] + int(np.round(w/2)) # xmin + width/2
        yc = bbox[1] + int(np.round(h/2)) # ymin + height/2
        
        yolo_boxes.append([xc/img_w, yc/img_h, w/img_w, h/img_h]) # x_center y_center width height
    
    return yolo_boxes

# Prepare the txt files for bounding box
for i in tqdm(range(len(df))):
    row = df.loc[i]
    # Get image id
    img_id = row.id
    # Get split
    split = row.split
    # Get image-level label
    label = row.image_level
    
    if row.split=='train':
        file_name = f'tmp/covid/labels/train/{row.id}.txt'
    else:
        file_name = f'tmp/covid/labels/valid/{row.id}.txt'
        
    
    if label=='opacity':
        # Get bboxes
        bboxes = get_bbox(row)
        # Scale bounding boxes
        scale_bboxes = scale_bbox(row, bboxes)
        # Format for YOLOv5
        yolo_bboxes = get_yolo_format_bbox(IMG_SIZE, IMG_SIZE, scale_bboxes)
        
        with open(file_name, 'w') as f:
            for bbox in yolo_bboxes:
                bbox = [1]+bbox
                bbox = [str(i) for i in bbox]
                bbox = ' '.join(bbox)
                f.write(bbox)
                f.write('\n')

100%|█████████████████████████████████████████████████████████████████████████████| 6334/6334 [00:14<00:00, 427.86it/s]


# 🚅 Train with W&B



#%cd tmp/yolov5/
```
--img {IMG_SIZE} \ # Input image size.
--batch {BATCH_SIZE} \ # Batch size
--epochs {EPOCHS} \ # Number of epochs
--data data.yaml \ # Configuration file
--weights yolov5s.pt \ # Model name
--save_period 1\ # Save model after interval
--project kaggle-siim-covid # W&B project name
```

In [7]:
os.chdir("D:\\Datasets\\SIIM_RSNA_Covid_Datasets\\tmp\\yolov5")
os.getcwd()

'D:\\Datasets\\SIIM_RSNA_Covid_Datasets\\tmp\\yolov5'

#### Run 1

Ensure that the 512 pixel image size can be handled here.

In [6]:
# Original Train
!python train.py --img {IMG_SIZE} \
                 --batch {BATCH_SIZE} \
                 --epochs {EPOCHS} \
                 --data data.yaml \
                 --weights yolov5s.pt \
                 --save_period 1\
                 --project SIIM_COVID_512_Runs

train: weights=yolov5s.pt, cfg=, data=data.yaml, hyp=data/hyps/hyp.scratch.yaml, epochs=50, batch_size=64, imgsz=512, rect=False, resume=False, nosave=False, noval=False, noautoanchor=False, evolve=None, bucket=, cache=None, image_weights=False, device=, multi_scale=False, single_cls=False, adam=False, sync_bn=False, workers=8, project=SIIM_COVID_512_Runs, entity=None, name=exp, exist_ok=False, quad=False, linear_lr=False, label_smoothing=0.0, upload_dataset=False, bbox_interval=-1, save_period=1, artifact_alias=latest, local_rank=-1, freeze=0
github: up to date with https://github.com/ultralytics/yolov5 

Plotting labels... 

autoanchor: Analyzing anchors... anchors/target = 4.76, Best Possible Recall (BPR) = 1.0000
                 all       1267       1582      0.145      0.285     0.0872     0.0169
Saving model artifact on epoch  1
                 all       1267       1582      0.299      0.336      0.232     0.0566
Saving model artifact on epoch  2
                 all       1267

YOLOv5  v5.0-350-gf409d8e torch 1.8.1 CUDA:0 (NVIDIA GeForce GTX 1080 Ti, 11264.0MB)

hyperparameters: lr0=0.01, lrf=0.2, momentum=0.937, weight_decay=0.0005, warmup_epochs=3.0, warmup_momentum=0.8, warmup_bias_lr=0.1, box=0.05, cls=0.5, cls_pw=1.0, obj=1.0, obj_pw=1.0, iou_t=0.2, anchor_t=4.0, fl_gamma=0.0, hsv_h=0.015, hsv_s=0.7, hsv_v=0.4, degrees=0.0, translate=0.1, scale=0.5, shear=0.0, perspective=0.0, flipud=0.0, fliplr=0.5, mosaic=1.0, mixup=0.0, copy_paste=0.0
TensorBoard: Start with 'tensorboard --logdir SIIM_COVID_512_Runs', view at http://localhost:6006/
wandb: Currently logged in as: ogk01 (use `wandb login --relogin` to force relogin)
wandb: wandb version 0.11.2 is available!  To upgrade, please run:
wandb:  $ pip install wandb --upgrade
wandb: Tracking run with wandb version 0.10.30
wandb: Syncing run lively-salad-2
wandb:  View project at https://wandb.ai/ogk01/SIIM_COVID_512_Runs
wandb:  View run at https://wandb.ai/ogk01/SIIM_COVID_512_Runs/runs/1l6hrlnf
wandb: Run da

Saving model artifact on epoch  14
                 all       1267       1582      0.471      0.419      0.364     0.0955
Saving model artifact on epoch  15
                 all       1267       1582      0.321      0.292      0.214     0.0524
Saving model artifact on epoch  16
                 all       1267       1582      0.367       0.39      0.293     0.0686
Saving model artifact on epoch  17
                 all       1267       1582      0.427      0.414      0.352     0.0929
Saving model artifact on epoch  18
                 all       1267       1582      0.532      0.434      0.433      0.126
Saving model artifact on epoch  19
                 all       1267       1582      0.495      0.451      0.395      0.106
Saving model artifact on epoch  20
                 all       1267       1582      0.508      0.399      0.387      0.108
Saving model artifact on epoch  21
                 all       1267       1582      0.516      0.444      0.407      0.111
Saving model artifact on


  2                -1  1     18816  models.common.C3                        [64, 64, 1]                   
  3                -1  1     73984  models.common.Conv                      [64, 128, 3, 2]               
  4                -1  1    156928  models.common.C3                        [128, 128, 3]                 
  5                -1  1    295424  models.common.Conv                      [128, 256, 3, 2]              
  6                -1  1    625152  models.common.C3                        [256, 256, 3]                 
  7                -1  1   1180672  models.common.Conv                      [256, 512, 3, 2]              
  8                -1  1    656896  models.common.SPP                       [512, 512, [5, 9, 13]]        
  9                -1  1   1182720  models.common.C3                        [512, 512, 1, False]          
 10                -1  1    131584  models.common.Conv                      [512, 256, 1, 1]              
 11                -1  1         0  

      0/49     7.97G   0.09374   0.02412   0.01589       158       512:  80%|########  | 64/80 [01:06<00:15,  1.02it/s]
      0/49     7.97G   0.09348    0.0241   0.01573       120       512:  80%|########  | 64/80 [01:07<00:15,  1.02it/s]
      0/49     7.97G   0.09348    0.0241   0.01573       120       512:  81%|########1 | 65/80 [01:07<00:14,  1.01it/s]
      0/49     7.97G   0.09325   0.02405   0.01557       106       512:  81%|########1 | 65/80 [01:08<00:14,  1.01it/s]
      0/49     7.97G   0.09325   0.02405   0.01557       106       512:  82%|########2 | 66/80 [01:08<00:13,  1.01it/s]
      0/49     7.97G     0.093    0.0241   0.01541       152       512:  82%|########2 | 66/80 [01:09<00:13,  1.01it/s]
      0/49     7.97G     0.093    0.0241   0.01541       152       512:  84%|########3 | 67/80 [01:09<00:12,  1.01it/s]
      0/49     7.97G   0.09276   0.02413   0.01526       140       512:  84%|########3 | 67/80 [01:10<00:12,  1.01it/s]
      0/49     7.97G   0.09276   0.02413

     17/49     9.19G   0.05131   0.01975  0.000132       153       512:  57%|#####7    | 46/80 [00:28<00:20,  1.63it/s]
     17/49     9.19G   0.05128   0.01977 0.0001319       147       512:  57%|#####7    | 46/80 [00:29<00:20,  1.63it/s]
     17/49     9.19G   0.05128   0.01977 0.0001319       147       512:  59%|#####8    | 47/80 [00:29<00:20,  1.63it/s]
     17/49     9.19G   0.05128   0.01973 0.0001317       122       512:  59%|#####8    | 47/80 [00:29<00:20,  1.63it/s]
     17/49     9.19G   0.05128   0.01973 0.0001317       122       512:  60%|######    | 48/80 [00:29<00:19,  1.62it/s]
     17/49     9.19G   0.05124   0.01976 0.0001316       153       512:  60%|######    | 48/80 [00:30<00:19,  1.62it/s]
     17/49     9.19G   0.05124   0.01976 0.0001316       153       512:  61%|######1   | 49/80 [00:30<00:19,  1.63it/s]
     17/49     9.19G   0.05123   0.01974 0.0001319       127       512:  61%|######1   | 49/80 [00:31<00:19,  1.63it/s]
     17/49     9.19G   0.05123   0.01974

     22/49     9.19G    0.0494   0.01952 0.0001105       145       512:  14%|#3        | 11/80 [00:06<00:36,  1.90it/s]
     22/49     9.19G   0.04957   0.01925 0.0001091       119       512:  14%|#3        | 11/80 [00:06<00:36,  1.90it/s]
     22/49     9.19G   0.04957   0.01925 0.0001091       119       512:  15%|#5        | 12/80 [00:06<00:35,  1.91it/s]
     22/49     9.19G   0.04947   0.01917 0.0001086       130       512:  15%|#5        | 12/80 [00:07<00:35,  1.91it/s]
     22/49     9.19G   0.04947   0.01917 0.0001086       130       512:  16%|#6        | 13/80 [00:07<00:35,  1.89it/s]
     22/49     9.19G   0.04948   0.01927  0.000108       138       512:  16%|#6        | 13/80 [00:07<00:35,  1.89it/s]
     22/49     9.19G   0.04948   0.01927  0.000108       138       512:  18%|#7        | 14/80 [00:07<00:36,  1.82it/s]
     22/49     9.19G   0.04923   0.01938 0.0001081       144       512:  18%|#7        | 14/80 [00:08<00:36,  1.82it/s]
     22/49     9.19G   0.04923   0.01938

     33/49     9.19G   0.04838   0.01907 5.973e-05       133       512:   1%|1         | 1/80 [00:01<00:40,  1.96it/s]
     33/49     9.19G   0.04838   0.01907 5.973e-05       133       512:   2%|2         | 2/80 [00:01<00:39,  1.96it/s]
     33/49     9.19G   0.04785   0.01877 6.264e-05       121       512:   2%|2         | 2/80 [00:01<00:39,  1.96it/s]
     33/49     9.19G   0.04785   0.01877 6.264e-05       121       512:   4%|3         | 3/80 [00:01<00:39,  1.95it/s]
     33/49     9.19G   0.04807    0.0193 6.389e-05       146       512:   4%|3         | 3/80 [00:02<00:39,  1.95it/s]
     33/49     9.19G   0.04807    0.0193 6.389e-05       146       512:   5%|5         | 4/80 [00:02<00:39,  1.94it/s]
     33/49     9.19G   0.04836   0.01976  6.51e-05       153       512:   5%|5         | 4/80 [00:02<00:39,  1.94it/s]
     33/49     9.19G   0.04836   0.01976  6.51e-05       153       512:   6%|6         | 5/80 [00:02<00:38,  1.93it/s]
     33/49     9.19G   0.04823   0.01947  6.57e-

     33/49     9.19G   0.04738   0.01944 6.654e-05       124       512:  96%|#########6| 77/80 [00:40<00:01,  1.84it/s]
     33/49     9.19G   0.04737   0.01942 6.649e-05       137       512:  96%|#########6| 77/80 [00:41<00:01,  1.84it/s]
     33/49     9.19G   0.04737   0.01942 6.649e-05       137       512:  98%|#########7| 78/80 [00:41<00:01,  1.85it/s]
     33/49     9.19G    0.0474   0.01943 6.648e-05       145       512:  98%|#########7| 78/80 [00:41<00:01,  1.85it/s]
     33/49     9.19G    0.0474   0.01943 6.648e-05       145       512:  99%|#########8| 79/80 [00:41<00:00,  1.87it/s]
     33/49     9.19G    0.0474   0.01947 6.661e-05        26       512:  99%|#########8| 79/80 [00:41<00:00,  1.87it/s]
     33/49     9.19G    0.0474   0.01947 6.661e-05        26       512: 100%|##########| 80/80 [00:41<00:00,  2.40it/s]
     33/49     9.19G    0.0474   0.01947 6.661e-05        26       512: 100%|##########| 80/80 [00:41<00:00,  1.91it/s]

               Class     Images     Lab

     34/49     9.19G   0.04723   0.01916 6.614e-05       128       512:  80%|########  | 64/80 [00:34<00:08,  1.88it/s]
     34/49     9.19G   0.04723   0.01916 6.614e-05       128       512:  81%|########1 | 65/80 [00:34<00:07,  1.89it/s]
     34/49     9.19G   0.04721   0.01917 6.619e-05       153       512:  81%|########1 | 65/80 [00:34<00:07,  1.89it/s]
     34/49     9.19G   0.04721   0.01917 6.619e-05       153       512:  82%|########2 | 66/80 [00:34<00:07,  1.91it/s]
     34/49     9.19G   0.04718   0.01915 6.611e-05       122       512:  82%|########2 | 66/80 [00:35<00:07,  1.91it/s]
     34/49     9.19G   0.04718   0.01915 6.611e-05       122       512:  84%|########3 | 67/80 [00:35<00:06,  1.92it/s]
     34/49     9.19G   0.04721   0.01917  6.61e-05       148       512:  84%|########3 | 67/80 [00:35<00:06,  1.92it/s]
     34/49     9.19G   0.04721   0.01917  6.61e-05       148       512:  85%|########5 | 68/80 [00:35<00:06,  1.92it/s]
     34/49     9.19G   0.04719   0.01919

### Hyperparameter Tuning (Multiple Runs)

#### Run 2

Learning Rate (lr0) = 0.02 <br> 
momentum = 0.5 <br>
warmup_epochs = 5 <br>
iou_threshold = 0.4 <br>
warmup_momentum = 0.25 <br>

In [8]:
# Manually Tune Hyperparameters to test

!python train.py --img {IMG_SIZE} \
                 --batch {BATCH_SIZE} \
                 --epochs {EPOCHS} \
                 --data data.yaml \
                 --weights yolov5s.pt \
                 --save_period 1\
                 --hyp data/hyps/hyp.scratch_1.yaml \
                 --project SIIM_COVID_512_Runs

train: weights=yolov5s.pt, cfg=, data=data.yaml, hyp=data/hyps/hyp.scratch_1.yaml, epochs=50, batch_size=64, imgsz=512, rect=False, resume=False, nosave=False, noval=False, noautoanchor=False, evolve=None, bucket=, cache=None, image_weights=False, device=, multi_scale=False, single_cls=False, adam=False, sync_bn=False, workers=8, project=SIIM_COVID_512_Runs, entity=None, name=exp, exist_ok=False, quad=False, linear_lr=False, label_smoothing=0.0, upload_dataset=False, bbox_interval=-1, save_period=1, artifact_alias=latest, local_rank=-1, freeze=0
github:  WARNING: code is out of date by 8 commits. Use 'git pull' to update or 'git clone https://github.com/ultralytics/yolov5' to download latest.

Plotting labels... 


From https://github.com/ultralytics/yolov5
   f409d8e..3e7c59a  master                  -> origin/master
 * [new branch]      batrlatom-patch-1       -> origin/batrlatom-patch-1
   5869629..504e828  exp/albumentations      -> origin/exp/albumentations
   b9cb7e1..2b170c9  python_version_CI_tests -> origin/python_version_CI_tests
YOLOv5  v5.0-350-gf409d8e torch 1.8.1 CUDA:0 (NVIDIA GeForce GTX 1080 Ti, 11264.0MB)

hyperparameters: lr0=0.02, lrf=0.2, momentum=0.5, weight_decay=0.0005, warmup_epochs=5.0, warmup_momentum=0.25, warmup_bias_lr=0.1, box=0.05, cls=0.5, cls_pw=1.0, obj=1.0, obj_pw=1.0, iou_t=0.4, anchor_t=4.0, fl_gamma=0.0, hsv_h=0.015, hsv_s=0.7, hsv_v=0.4, degrees=0.0, translate=0.1, scale=0.5, shear=0.0, perspective=0.0, flipud=0.0, fliplr=0.5, mosaic=1.0, mixup=0.0, copy_paste=0.0
TensorBoard: Start with 'tensorboard --logdir SIIM_COVID_512_Runs', view at http://localhost:6006/
wandb: Currently logged in as: ogk01 (use `wandb login --relogin` to force relogin)
wandb: wandb 


autoanchor: Analyzing anchors... anchors/target = 4.76, Best Possible Recall (BPR) = 1.0000
                 all       1267       1582       0.12      0.212     0.0631     0.0112
Saving model artifact on epoch  1
                 all       1267       1582      0.226      0.323      0.173     0.0378
Saving model artifact on epoch  2
                 all       1267       1582       0.36      0.326      0.233     0.0577
Saving model artifact on epoch  3
                 all       1267       1582      0.336      0.329       0.24     0.0607
Saving model artifact on epoch  4
                 all       1267       1582      0.403      0.327       0.25     0.0648
Saving model artifact on epoch  5
                 all       1267       1582       0.37      0.382      0.283      0.071
Saving model artifact on epoch  6
                 all       1267       1582      0.488      0.413      0.357     0.0926
Saving model artifact on epoch  7
                 all       1267       1582      0.261      0


  1                -1  1     18560  models.common.Conv                      [32, 64, 3, 2]                
  2                -1  1     18816  models.common.C3                        [64, 64, 1]                   
  3                -1  1     73984  models.common.Conv                      [64, 128, 3, 2]               
  4                -1  1    156928  models.common.C3                        [128, 128, 3]                 
  5                -1  1    295424  models.common.Conv                      [128, 256, 3, 2]              
  6                -1  1    625152  models.common.C3                        [256, 256, 3]                 
  7                -1  1   1180672  models.common.Conv                      [256, 512, 3, 2]              
  8                -1  1    656896  models.common.SPP                       [512, 512, [5, 9, 13]]        
  9                -1  1   1182720  models.common.C3                        [512, 512, 1, False]          
 10                -1  1    131584  

      0/49     7.97G    0.1127   0.02354   0.02799       156       512:  41%|####1     | 33/80 [00:27<00:24,  1.92it/s]
      0/49     7.97G    0.1127   0.02354   0.02799       156       512:  42%|####2     | 34/80 [00:27<00:23,  1.94it/s]
      0/49     7.97G    0.1123   0.02357    0.0278       139       512:  42%|####2     | 34/80 [00:27<00:23,  1.94it/s]
      0/49     7.97G    0.1123   0.02357    0.0278       139       512:  44%|####3     | 35/80 [00:27<00:23,  1.95it/s]
      0/49     7.97G    0.1118   0.02359   0.02758       134       512:  44%|####3     | 35/80 [00:28<00:23,  1.95it/s]
      0/49     7.97G    0.1118   0.02359   0.02758       134       512:  45%|####5     | 36/80 [00:28<00:22,  1.94it/s]
      0/49     7.97G    0.1114   0.02356   0.02739       129       512:  45%|####5     | 36/80 [00:28<00:22,  1.94it/s]
      0/49     7.97G    0.1114   0.02356   0.02739       129       512:  46%|####6     | 37/80 [00:28<00:22,  1.95it/s]
      0/49     7.97G    0.1109   0.02357

...

     19/49     9.19G   0.05238   0.01961 0.0003771       124       512:  31%|###1      | 25/80 [00:13<00:28,  1.90it/s]
     19/49     9.19G   0.05238   0.01961 0.0003771       124       512:  32%|###2      | 26/80 [00:13<00:28,  1.91it/s]
     19/49     9.19G   0.05246   0.01967 0.0003752       148       512:  32%|###2      | 26/80 [00:14<00:28,  1.91it/s]
     19/49     9.19G   0.05246   0.01967 0.0003752       148       512:  34%|###3      | 27/80 [00:14<00:27,  1.92it/s]
     19/49     9.19G   0.05252   0.01958 0.0003766       123       512:  34%|###3      | 27/80 [00:14<00:27,  1.92it/s]
     19/49     9.19G   0.05252   0.01958 0.0003766       123       512:  35%|###5      | 28/80 [00:14<00:26,  1.93it/s]
     19/49     9.19G   0.05253   0.01956 0.0003771       131       512:  35%|###5      | 28/80 [00:15<00:26,  1.93it/s]
     19/49     9.19G   0.05253   0.01956 0.0003771       131       512:  36%|###6      | 29/80 [00:15<00:26,  1.93it/s]
     19/49     9.19G   0.05248   0.01968

     31/49     9.19G   0.04838   0.01911 0.0001814       142       512:  94%|#########3| 75/80 [00:39<00:02,  1.93it/s]
     31/49     9.19G    0.0484   0.01916  0.000181       151       512:  94%|#########3| 75/80 [00:39<00:02,  1.93it/s]
     31/49     9.19G    0.0484   0.01916  0.000181       151       512:  95%|#########5| 76/80 [00:39<00:02,  1.93it/s]
     31/49     9.19G   0.04841   0.01921 0.0001811       171       512:  95%|#########5| 76/80 [00:40<00:02,  1.93it/s]
     31/49     9.19G   0.04841   0.01921 0.0001811       171       512:  96%|#########6| 77/80 [00:40<00:01,  1.94it/s]
     31/49     9.19G   0.04843   0.01919 0.0001811       126       512:  96%|#########6| 77/80 [00:40<00:01,  1.94it/s]
     31/49     9.19G   0.04843   0.01919 0.0001811       126       512:  98%|#########7| 78/80 [00:40<00:01,  1.93it/s]
     31/49     9.19G    0.0484   0.01918 0.0001812       137       512:  98%|#########7| 78/80 [00:41<00:01,  1.93it/s]
     31/49     9.19G    0.0484   0.01918

               Class     Images     Labels          P          R     mAP@.5 mAP@.5:.95:  80%|########  | 8/10 [00:05<00:01,  1.48it/s]
               Class     Images     Labels          P          R     mAP@.5 mAP@.5:.95:  90%|######### | 9/10 [00:06<00:00,  1.49it/s]
               Class     Images     Labels          P          R     mAP@.5 mAP@.5:.95: 100%|##########| 10/10 [00:06<00:00,  1.56it/s]
               Class     Images     Labels          P          R     mAP@.5 mAP@.5:.95: 100%|##########| 10/10 [00:06<00:00,  1.51it/s]

     Epoch   gpu_mem       box       obj       cls    labels  img_size

  0%|          | 0/80 [00:00<?, ?it/s]
     33/49     9.19G   0.04439   0.01866 0.0001457       136       512:   0%|          | 0/80 [00:00<?, ?it/s]
     33/49     9.19G   0.04439   0.01866 0.0001457       136       512:   1%|1         | 1/80 [00:00<00:40,  1.95it/s]
     33/49     9.19G   0.04787    0.0189 0.0001549       133       512:   1%|1         | 1/80 [00:01<00:40,  1.95it/

     36/49     9.19G   0.04674   0.01959 0.0001354       142       512:   9%|8         | 7/80 [00:03<00:37,  1.95it/s]
     36/49     9.19G   0.04692   0.01943 0.0001342       133       512:   9%|8         | 7/80 [00:04<00:37,  1.95it/s]
     36/49     9.19G   0.04692   0.01943 0.0001342       133       512:  10%|#         | 8/80 [00:04<00:36,  1.95it/s]
     36/49     9.19G   0.04719    0.0192 0.0001349       120       512:  10%|#         | 8/80 [00:04<00:36,  1.95it/s]
     36/49     9.19G   0.04719    0.0192 0.0001349       120       512:  11%|#1        | 9/80 [00:04<00:37,  1.92it/s]
     36/49     9.19G    0.0475   0.01956 0.0001365       162       512:  11%|#1        | 9/80 [00:05<00:37,  1.92it/s]
     36/49     9.19G    0.0475   0.01956 0.0001365       162       512:  12%|#2        | 10/80 [00:05<00:37,  1.87it/s]
     36/49     9.19G   0.04749   0.01954 0.0001369       123       512:  12%|#2        | 10/80 [00:05<00:37,  1.87it/s]
     36/49     9.19G   0.04749   0.01954 0.000

wandb: / 2716.27MB of 2716.27MB uploaded (0.00MB deduped)
wandb: - 2716.27MB of 2716.27MB uploaded (0.00MB deduped)
wandb:                                                                                
wandb: Find user logs for this run at: D:\Datasets\SIIM_RSNA_Covid_Datasets\tmp\yolov5\wandb\run-20210812_212450-xa785iux\logs\debug.log
wandb: Find internal logs for this run at: D:\Datasets\SIIM_RSNA_Covid_Datasets\tmp\yolov5\wandb\run-20210812_212450-xa785iux\logs\debug-internal.log
wandb: Run summary:
wandb:                 train/box_loss 0.04534
wandb:                 train/obj_loss 0.01895
wandb:                 train/cls_loss 8e-05
wandb:              metrics/precision 0.51401
wandb:                 metrics/recall 0.4665
wandb:                metrics/mAP_0.5 0.43431
wandb:           metrics/mAP_0.5:0.95 0.12926
wandb:                   val/box_loss 0.0552
wandb:                   val/obj_loss 0.01064
wandb:                   val/cls_loss 7e-05
wandb:                          x/lr

#### Run 3

Increases the learning rate, as well as other properties to speed up learning rate at the end. 

In [ ]:
# Already Run
!python train.py --img {IMG_SIZE} \
                 --batch {BATCH_SIZE} \
                 --epochs {EPOCHS} \
                 --data data.yaml \
                 --weights yolov5s.pt \
                 --save_period 1\
                 --hyp data/hyps/hyp.scratch_2.yaml \
                 --project SIIM_COVID_512_Runs

#### Run 4

In [13]:
!python train.py --img {IMG_SIZE} \
                 --batch {BATCH_SIZE} \
                 --epochs {EPOCHS} \
                 --data data.yaml \
                 --weights yolov5s.pt \
                 --save_period 1\
                 --hyp data/hyps/hyp.scratch_3.yaml \
                 --project SIIM_COVID_512_Runs

train: weights=yolov5s.pt, cfg=, data=data.yaml, hyp=data/hyps/hyp.scratch_3.yaml, epochs=50, batch_size=64, imgsz=512, rect=False, resume=False, nosave=False, noval=False, noautoanchor=False, evolve=None, bucket=, cache=None, image_weights=False, device=, multi_scale=False, single_cls=False, adam=False, sync_bn=False, workers=8, project=SIIM_COVID_512_Runs, entity=None, name=exp, exist_ok=False, quad=False, linear_lr=False, label_smoothing=0.0, upload_dataset=False, bbox_interval=-1, save_period=1, artifact_alias=latest, local_rank=-1, freeze=0
github:  WARNING: code is out of date by 14 commits. Use 'git pull' to update or 'git clone https://github.com/ultralytics/yolov5' to download latest.

Plotting labels... 

autoanchor: Analyzing anchors... anchors/target = 4.76, Best Possible Recall (BPR) = 1.0000
                 all       1267       1582      0.187      0.243      0.113     0.0233
Saving model artifact on epoch  1
                 all       1267       1582      0.362      0.3

From https://github.com/ultralytics/yolov5
   63e09fd..2da4e7a  master     -> origin/master
YOLOv5  v5.0-350-gf409d8e torch 1.8.1 CUDA:0 (NVIDIA GeForce GTX 1080 Ti, 11264.0MB)

hyperparameters: lr0=0.08, lrf=0.3, momentum=0.5, weight_decay=0.005, warmup_epochs=10, warmup_momentum=0.5, warmup_bias_lr=0.2, box=0.05, cls=0.5, cls_pw=1.0, obj=1.0, obj_pw=1.0, iou_t=0.75, anchor_t=4.0, fl_gamma=0.0, hsv_h=0.015, hsv_s=0.7, hsv_v=0.4, degrees=0.0, translate=0.1, scale=0.5, shear=0.0, perspective=0.0, flipud=0.0, fliplr=0.5, mosaic=1.0, mixup=0.0, copy_paste=0.0
TensorBoard: Start with 'tensorboard --logdir SIIM_COVID_512_Runs', view at http://localhost:6006/
wandb: Currently logged in as: ogk01 (use `wandb login --relogin` to force relogin)
wandb: wandb version 0.12.0 is available!  To upgrade, please run:
wandb:  $ pip install wandb --upgrade
wandb: Tracking run with wandb version 0.10.30
wandb: Syncing run super-night-5
wandb:  View project at https://wandb.ai/ogk01/SIIM_COVID_512_Runs
wa

Saving model artifact on epoch  22
                 all       1267       1582      0.394       0.41       0.32     0.0915
Saving model artifact on epoch  23
                 all       1267       1582      0.165      0.272      0.122      0.024
Saving model artifact on epoch  24
                 all       1267       1582      0.454      0.395      0.343     0.0875
Saving model artifact on epoch  25
                 all       1267       1582      0.398      0.377      0.319      0.083
Saving model artifact on epoch  26
                 all       1267       1582      0.379      0.411      0.324     0.0909
Saving model artifact on epoch  27
                 all       1267       1582      0.456      0.413      0.349     0.0899
Saving model artifact on epoch  28
                 all       1267       1582      0.392      0.382      0.314     0.0745
Saving model artifact on epoch  29
                 all       1267       1582      0.423      0.484      0.398      0.109
Saving model artifact on


      0/49     7.97G    0.1003   0.02412   0.02143       139       512:  36%|###6      | 29/80 [00:18<00:27,  1.88it/s]
      0/49     7.97G    0.1003   0.02412   0.02143       139       512:  38%|###7      | 30/80 [00:18<00:27,  1.83it/s]
      0/49     7.97G   0.09957    0.0241   0.02106       128       512:  38%|###7      | 30/80 [00:19<00:27,  1.83it/s]
      0/49     7.97G   0.09957    0.0241   0.02106       128       512:  39%|###8      | 31/80 [00:19<00:27,  1.81it/s]
      0/49     7.97G   0.09904   0.02411   0.02071       132       512:  39%|###8      | 31/80 [00:20<00:27,  1.81it/s]
      0/49     7.97G   0.09904   0.02411   0.02071       132       512:  40%|####      | 32/80 [00:20<00:26,  1.84it/s]
      0/49     7.97G   0.09836   0.02418   0.02036       139       512:  40%|####      | 32/80 [00:20<00:26,  1.84it/s]
      0/49     7.97G   0.09836   0.02418   0.02036       139       512:  41%|####1     | 33/80 [00:20<00:25,  1.84it/s]
      0/49     7.97G   0.09781   0.0242

#### Run 5

This run tests a slower learning rate and downscales all learning and momentum parameters. Changed IoU threshold to 0.25, to see what effect this would have.

In [15]:
!python train.py --img {IMG_SIZE} \
                 --batch {BATCH_SIZE} \
                 --epochs {EPOCHS} \
                 --data data.yaml \
                 --weights yolov5s.pt \
                 --save_period 1\
                 --hyp data/hyps/hyp.scratch_4.yaml \
                 --project SIIM_COVID_512_Runs

train: weights=yolov5s.pt, cfg=, data=data.yaml, hyp=data/hyps/hyp.scratch_4.yaml, epochs=50, batch_size=64, imgsz=512, rect=False, resume=False, nosave=False, noval=False, noautoanchor=False, evolve=None, bucket=, cache=None, image_weights=False, device=, multi_scale=False, single_cls=False, adam=False, sync_bn=False, workers=8, project=SIIM_COVID_512_Runs, entity=None, name=exp, exist_ok=False, quad=False, linear_lr=False, label_smoothing=0.0, upload_dataset=False, bbox_interval=-1, save_period=1, artifact_alias=latest, local_rank=-1, freeze=0
github:  WARNING: code is out of date by 16 commits. Use 'git pull' to update or 'git clone https://github.com/ultralytics/yolov5' to download latest.

Plotting labels... 

autoanchor: Analyzing anchors... anchors/target = 4.76, Best Possible Recall (BPR) = 1.0000
                 all       1267       1582     0.0262      0.115     0.0136    0.00226
Saving model artifact on epoch  1
                 all       1267       1582       0.15      0.2

From https://github.com/ultralytics/yolov5
   2da4e7a..24bea5e  master     -> origin/master
YOLOv5  v5.0-350-gf409d8e torch 1.8.1 CUDA:0 (NVIDIA GeForce GTX 1080 Ti, 11264.0MB)

hyperparameters: lr0=0.01, lrf=0.2, momentum=0.2, weight_decay=0.0005, warmup_epochs=5, warmup_momentum=0.15, warmup_bias_lr=0.1, box=0.05, cls=0.5, cls_pw=1.0, obj=1.0, obj_pw=1.0, iou_t=0.25, anchor_t=4.0, fl_gamma=0.0, hsv_h=0.015, hsv_s=0.7, hsv_v=0.4, degrees=0.0, translate=0.1, scale=0.5, shear=0.0, perspective=0.0, flipud=0.0, fliplr=0.5, mosaic=1.0, mixup=0.0, copy_paste=0.0
TensorBoard: Start with 'tensorboard --logdir SIIM_COVID_512_Runs', view at http://localhost:6006/
wandb: Currently logged in as: ogk01 (use `wandb login --relogin` to force relogin)
wandb: wandb version 0.12.0 is available!  To upgrade, please run:
wandb:  $ pip install wandb --upgrade
wandb: Tracking run with wandb version 0.10.30
wandb: Syncing run autumn-monkey-6
wandb:  View project at https://wandb.ai/ogk01/SIIM_COVID_512_Runs

                 all       1267       1582      0.534      0.417      0.421      0.117
Saving model artifact on epoch  25
                 all       1267       1582      0.501      0.482      0.439      0.126
Saving model artifact on epoch  26
                 all       1267       1582      0.486      0.433      0.408      0.115
Saving model artifact on epoch  27
                 all       1267       1582      0.512      0.488      0.445      0.132
Saving model artifact on epoch  28
                 all       1267       1582      0.537      0.454      0.437      0.126
Saving model artifact on epoch  29
                 all       1267       1582      0.551      0.467      0.445      0.132
Saving model artifact on epoch  30
                 all       1267       1582      0.547      0.446      0.443       0.13
Saving model artifact on epoch  31
                 all       1267       1582      0.558      0.473      0.455      0.137
Saving model artifact on epoch  32
                 all    

Transferred 356/362 items from yolov5s.pt
Scaled weight_decay = 0.0005
optimizer: SGD with parameter groups 59 weight, 62 weight (no decay), 62 bias
albumentations: version 1.0.3 required by YOLOv5, but version 1.0.0 is currently installed

train: Scanning '..\covid\labels\train.cache' images and labels... 3435 found, 1632 missing, 0 empty, 0 corrupted: 100%|##########| 5067/5067 [00:00<?, ?it/s]
train: Scanning '..\covid\labels\train.cache' images and labels... 3435 found, 1632 missing, 0 empty, 0 corrupted: 100%|##########| 5067/5067 [00:00<?, ?it/s]

val: Scanning '..\covid\labels\valid.cache' images and labels... 859 found, 408 missing, 0 empty, 0 corrupted: 100%|##########| 1267/1267 [00:00<?, ?it/s]
val: Scanning '..\covid\labels\valid.cache' images and labels... 859 found, 408 missing, 0 empty, 0 corrupted: 100%|##########| 1267/1267 [00:00<?, ?it/s]
Image sizes 512 train, 512 val
Using 8 dataloader workers
Logging results to SIIM_COVID_512_Runs\exp6
Starting training for 50 epo

#### Run 6

This run tests a slower learning rate and downscales all learning and momentum parameters, for 75 epochs, but raises the threshold back to 0.50

In [8]:
!python train.py --img {IMG_SIZE} \
                 --batch {BATCH_SIZE} \
                 --epochs {EPOCHS} \
                 --data data.yaml \
                 --weights yolov5s.pt \
                 --save_period 1\
                 --hyp data/hyps/hyp.scratch_4.yaml \
                 --project SIIM_COVID_512_Runs

train: weights=yolov5s.pt, cfg=, data=data.yaml, hyp=data/hyps/hyp.scratch_4.yaml, epochs=75, batch_size=64, imgsz=512, rect=False, resume=False, nosave=False, noval=False, noautoanchor=False, evolve=None, bucket=, cache=None, image_weights=False, device=, multi_scale=False, single_cls=False, adam=False, sync_bn=False, workers=8, project=SIIM_COVID_512_Runs, entity=None, name=exp, exist_ok=False, quad=False, linear_lr=False, label_smoothing=0.0, upload_dataset=False, bbox_interval=-1, save_period=1, artifact_alias=latest, local_rank=-1, freeze=0
github:  WARNING: code is out of date by 19 commits. Use 'git pull' to update or 'git clone https://github.com/ultralytics/yolov5' to download latest.

Plotting labels... 

autoanchor: Analyzing anchors... anchors/target = 4.76, Best Possible Recall (BPR) = 1.0000
                 all       1267       1582     0.0172      0.116    0.00926    0.00139
Saving model artifact on epoch  1
                 all       1267       1582      0.177      0.2

YOLOv5  v5.0-350-gf409d8e torch 1.8.1 CUDA:0 (NVIDIA GeForce GTX 1080 Ti, 11264.0MB)

hyperparameters: lr0=0.01, lrf=0.2, momentum=0.2, weight_decay=0.0005, warmup_epochs=5, warmup_momentum=0.15, warmup_bias_lr=0.1, box=0.05, cls=0.5, cls_pw=1.0, obj=1.0, obj_pw=1.0, iou_t=0.5, anchor_t=4.0, fl_gamma=0.0, hsv_h=0.015, hsv_s=0.7, hsv_v=0.4, degrees=0.0, translate=0.1, scale=0.5, shear=0.0, perspective=0.0, flipud=0.0, fliplr=0.5, mosaic=1.0, mixup=0.0, copy_paste=0.0
TensorBoard: Start with 'tensorboard --logdir SIIM_COVID_512_Runs', view at http://localhost:6006/
wandb: Currently logged in as: ogk01 (use `wandb login --relogin` to force relogin)
wandb: wandb version 0.12.0 is available!  To upgrade, please run:
wandb:  $ pip install wandb --upgrade
wandb: Tracking run with wandb version 0.10.30
wandb: Syncing run atomic-serenity-9
wandb:  View project at https://wandb.ai/ogk01/SIIM_COVID_512_Runs
wandb:  View run at https://wandb.ai/ogk01/SIIM_COVID_512_Runs/runs/zm6gd2xy
wandb: Run da


Saving model artifact on epoch  27
                 all       1267       1582      0.484      0.503      0.449      0.132
Saving model artifact on epoch  28
                 all       1267       1582      0.547      0.461      0.451       0.13
Saving model artifact on epoch  29
                 all       1267       1582      0.496      0.476      0.442      0.132
Saving model artifact on epoch  30
                 all       1267       1582      0.534      0.474      0.455       0.14
Saving model artifact on epoch  31
                 all       1267       1582      0.511      0.489      0.447      0.134
Saving model artifact on epoch  32
                 all       1267       1582      0.505      0.437      0.412      0.117
Saving model artifact on epoch  33
                 all       1267       1582      0.517      0.464      0.441      0.128
Saving model artifact on epoch  34
                 all       1267       1582      0.526       0.47       0.44      0.131
Saving model artifact o

      0/74     7.97G    0.1199   0.02363   0.03152       147       512:  19%|#8        | 15/80 [00:10<00:37,  1.74it/s]
      0/74     7.97G    0.1199   0.02363   0.03152       147       512:  20%|##        | 16/80 [00:10<00:36,  1.74it/s]
      0/74     7.97G    0.1197   0.02365   0.03139       159       512:  20%|##        | 16/80 [00:11<00:36,  1.74it/s]
      0/74     7.97G    0.1197   0.02365   0.03139       159       512:  21%|##1       | 17/80 [00:11<00:36,  1.72it/s]
      0/74     7.97G    0.1195   0.02364   0.03125       144       512:  21%|##1       | 17/80 [00:12<00:36,  1.72it/s]
      0/74     7.97G    0.1195   0.02364   0.03125       144       512:  22%|##2       | 18/80 [00:12<00:36,  1.72it/s]
      0/74     7.97G    0.1192   0.02361   0.03117       129       512:  22%|##2       | 18/80 [00:12<00:36,  1.72it/s]
      0/74     7.97G    0.1192   0.02361   0.03117       129       512:  24%|##3       | 19/80 [00:12<00:34,  1.75it/s]
      0/74     7.97G    0.1191   0.02359

      0/74     7.97G     0.103   0.02383   0.02307        22       512: 100%|##########| 80/80 [00:45<00:00,  1.76it/s]

               Class     Images     Labels          P          R     mAP@.5 mAP@.5:.95:   0%|          | 0/10 [00:00<?, ?it/s]
               Class     Images     Labels          P          R     mAP@.5 mAP@.5:.95:  10%|#         | 1/10 [00:01<00:09,  1.09s/it]
               Class     Images     Labels          P          R     mAP@.5 mAP@.5:.95:  20%|##        | 2/10 [00:02<00:08,  1.06s/it]
               Class     Images     Labels          P          R     mAP@.5 mAP@.5:.95:  30%|###       | 3/10 [00:03<00:07,  1.05s/it]
               Class     Images     Labels          P          R     mAP@.5 mAP@.5:.95:  40%|####      | 4/10 [00:04<00:06,  1.03s/it]
               Class     Images     Labels          P          R     mAP@.5 mAP@.5:.95:  50%|#####     | 5/10 [00:05<00:05,  1.02s/it]
               Class     Images     Labels          P          R     mAP@.5 m

...

     34/74     9.19G   0.04979   0.01944 0.0002319       141       512:  92%|#########2| 74/80 [00:38<00:03,  1.95it/s]
     34/74     9.19G   0.04974   0.01944  0.000232       130       512:  92%|#########2| 74/80 [00:39<00:03,  1.95it/s]
     34/74     9.19G   0.04974   0.01944  0.000232       130       512:  94%|#########3| 75/80 [00:39<00:02,  1.95it/s]
     34/74     9.19G   0.04975   0.01946 0.0002318       140       512:  94%|#########3| 75/80 [00:39<00:02,  1.95it/s]
     34/74     9.19G   0.04975   0.01946 0.0002318       140       512:  95%|#########5| 76/80 [00:39<00:02,  1.95it/s]
     34/74     9.19G   0.04973    0.0195 0.0002315       173       512:  95%|#########5| 76/80 [00:40<00:02,  1.95it/s]
     34/74     9.19G   0.04973    0.0195 0.0002315       173       512:  96%|#########6| 77/80 [00:40<00:01,  1.91it/s]
     34/74     9.19G   0.04975   0.01947 0.0002312       117       512:  96%|#########6| 77/80 [00:40<00:01,  1.91it/s]
     34/74     9.19G   0.04975   0.01947

  0%|          | 0/80 [00:00<?, ?it/s]
     52/74     9.19G   0.04663   0.02014 0.0001322       142       512:   0%|          | 0/80 [00:00<?, ?it/s]
     52/74     9.19G   0.04663   0.02014 0.0001322       142       512:   1%|1         | 1/80 [00:00<00:40,  1.96it/s]
     52/74     9.19G   0.04837   0.01932 0.0001325       121       512:   1%|1         | 1/80 [00:01<00:40,  1.96it/s]
     52/74     9.19G   0.04837   0.01932 0.0001325       121       512:   2%|2         | 2/80 [00:01<00:39,  1.96it/s]
     52/74     9.19G   0.04764   0.01956 0.0001318       136       512:   2%|2         | 2/80 [00:01<00:39,  1.96it/s]
     52/74     9.19G   0.04764   0.01956 0.0001318       136       512:   4%|3         | 3/80 [00:01<00:39,  1.96it/s]
     52/74     9.19G   0.04837    0.0196 0.0001302       141       512:   4%|3         | 3/80 [00:02<00:39,  1.96it/s]
     52/74     9.19G   0.04837    0.0196 0.0001302       141       512:   5%|5         | 4/80 [00:02<00:38,  1.96it/s]
     52/74     9.

     53/74     9.19G   0.04715   0.01945 0.0001207       135       512:  56%|#####6    | 45/80 [00:24<00:19,  1.84it/s]
     53/74     9.19G   0.04715   0.01945 0.0001207       135       512:  57%|#####7    | 46/80 [00:24<00:18,  1.81it/s]
     53/74     9.19G   0.04711   0.01941 0.0001207       125       512:  57%|#####7    | 46/80 [00:24<00:18,  1.81it/s]
     53/74     9.19G   0.04711   0.01941 0.0001207       125       512:  59%|#####8    | 47/80 [00:24<00:18,  1.81it/s]
     53/74     9.19G   0.04709   0.01942 0.0001206       144       512:  59%|#####8    | 47/80 [00:25<00:18,  1.81it/s]
     53/74     9.19G   0.04709   0.01942 0.0001206       144       512:  60%|######    | 48/80 [00:25<00:17,  1.82it/s]
     53/74     9.19G   0.04701   0.01942 0.0001205       138       512:  60%|######    | 48/80 [00:25<00:17,  1.82it/s]
     53/74     9.19G   0.04701   0.01942 0.0001205       138       512:  61%|######1   | 49/80 [00:25<00:16,  1.85it/s]
     53/74     9.19G   0.04701    0.0194

     70/74     9.19G   0.04568   0.01944 7.618e-05        20       512: 100%|##########| 80/80 [00:41<00:00,  2.49it/s]
     70/74     9.19G   0.04568   0.01944 7.618e-05        20       512: 100%|##########| 80/80 [00:41<00:00,  1.95it/s]

               Class     Images     Labels          P          R     mAP@.5 mAP@.5:.95:   0%|          | 0/10 [00:00<?, ?it/s]
               Class     Images     Labels          P          R     mAP@.5 mAP@.5:.95:  10%|#         | 1/10 [00:00<00:05,  1.55it/s]
               Class     Images     Labels          P          R     mAP@.5 mAP@.5:.95:  20%|##        | 2/10 [00:01<00:05,  1.52it/s]
               Class     Images     Labels          P          R     mAP@.5 mAP@.5:.95:  30%|###       | 3/10 [00:02<00:04,  1.50it/s]
               Class     Images     Labels          P          R     mAP@.5 mAP@.5:.95:  40%|####      | 4/10 [00:02<00:04,  1.49it/s]
               Class     Images     Labels          P          R     mAP@.5 mAP@.5:.95:  50%

     72/74     9.19G    0.0464   0.01922 6.936e-05       148       512:   8%|7         | 6/80 [00:03<00:37,  1.96it/s]
     72/74     9.19G    0.0464   0.01922 6.936e-05       148       512:   9%|8         | 7/80 [00:03<00:37,  1.96it/s]
     72/74     9.19G   0.04627   0.01896 6.955e-05       125       512:   9%|8         | 7/80 [00:04<00:37,  1.96it/s]
     72/74     9.19G   0.04627   0.01896 6.955e-05       125       512:  10%|#         | 8/80 [00:04<00:36,  1.96it/s]
     72/74     9.19G   0.04648   0.01878 7.011e-05       132       512:  10%|#         | 8/80 [00:04<00:36,  1.96it/s]
     72/74     9.19G   0.04648   0.01878 7.011e-05       132       512:  11%|#1        | 9/80 [00:04<00:36,  1.96it/s]
     72/74     9.19G    0.0466    0.0188 7.059e-05       141       512:  11%|#1        | 9/80 [00:05<00:36,  1.96it/s]
     72/74     9.19G    0.0466    0.0188 7.059e-05       141       512:  12%|#2        | 10/80 [00:05<00:35,  1.96it/s]
     72/74     9.19G   0.04645   0.01877 7.081e

## Model Saved Automatically as Artifact

Since it's a kernel based competition, you can easily download the best model from the W&B Artifacts UI and upload as a Kaggle dataset that you can load in your inference kernel (internel disabled).

### [Path to saved model $\rightarrow$](https://wandb.ai/ayush-thakur/kaggle-siim-covid/artifacts/model/run_jbt74n7q_model/4c3ca5752dba99bd227e)

![img](https://i.imgur.com/KhRLQvR.png)

> 📍 Download the model with the `best` alias tagged to it. 

# Inference

You will probably use a `Submission.ipynb` kernel to run all the predictions. After training a YOLOv5 based object detector -> head to the artifacts page and download the best model -> upload the model as a Kaggle dataset -> Use it with the submission folder. 

> 📍 Note that you might have to clone the YOLOv5 repository in a Kaggle dataset as well. 

In this section, I will show you how you can do the inference and modify the predicted bounding box coordinates.

In [10]:
# absolute path
TEST_PATH = 'D:\\Datasets\\SIIM_RSNA_Covid_Datasets\\test_jpeg_512'

Optimizer stripped from SIIM_COVID_512_Runs\exp4\weights\last.pt, 14.4MB
Optimizer stripped from SIIM_COVID_512_Runs\exp4\weights\best.pt, 14.4MB



      0/49     7.97G   0.08723   0.02439   0.01327       142       512:  96%|#########6| 77/80 [00:48<00:01,  1.94it/s]
      0/49     7.97G   0.08705   0.02439   0.01314       138       512:  96%|#########6| 77/80 [00:48<00:01,  1.94it/s]
      0/49     7.97G   0.08705   0.02439   0.01314       138       512:  98%|#########7| 78/80 [00:48<00:01,  1.95it/s]
      0/49     7.97G   0.08682   0.02438   0.01301       132       512:  98%|#########7| 78/80 [00:49<00:01,  1.95it/s]
      0/49     7.97G   0.08682   0.02438   0.01301       132       512:  99%|#########8| 79/80 [00:49<00:00,  1.95it/s]
      0/49     7.97G   0.08672   0.02435   0.01289        22       512:  99%|#########8| 79/80 [00:49<00:00,  1.95it/s]
      0/49     7.97G   0.08672   0.02435   0.01289        22       512: 100%|##########| 80/80 [00:49<00:00,  2.51it/s]
      0/49     7.97G   0.08672   0.02435   0.01289        22       512: 100%|##########| 80/80 [00:49<00:00,  1.62it/s]

               Class     Images     Lab

      1/49     9.19G   0.06779   0.02325  0.002154       156       512:  84%|########3 | 67/80 [00:35<00:06,  1.91it/s]
      1/49     9.19G   0.06779   0.02325  0.002154       156       512:  85%|########5 | 68/80 [00:35<00:06,  1.89it/s]
      1/49     9.19G   0.06768   0.02322  0.002143       127       512:  85%|########5 | 68/80 [00:36<00:06,  1.89it/s]
      1/49     9.19G   0.06768   0.02322  0.002143       127       512:  86%|########6 | 69/80 [00:36<00:05,  1.89it/s]
      1/49     9.19G   0.06771   0.02321  0.002135       144       512:  86%|########6 | 69/80 [00:37<00:05,  1.89it/s]
      1/49     9.19G   0.06771   0.02321  0.002135       144       512:  88%|########7 | 70/80 [00:37<00:05,  1.91it/s]
      1/49     9.19G   0.06776   0.02322  0.002131       145       512:  88%|########7 | 70/80 [00:37<00:05,  1.91it/s]
      1/49     9.19G   0.06776   0.02322  0.002131       145       512:  89%|########8 | 71/80 [00:37<00:04,  1.90it/s]
      1/49     9.19G   0.06775   0.02318

Since I am training the model in this kernel itself, I will not be using the method that I have described above. The best model is saved in the directory `project_name/exp*/weights/best.pt`. In `exp*`, * can be 1, 2, etc. 

In [11]:
MODEL_PATH = 'SIIM_COVID_512_Runs/exp4/weights/best.pt'


      3/49     9.19G   0.06124   0.02132  0.001216       143       512:   6%|6         | 5/80 [00:02<00:43,  1.71it/s]
      3/49     9.19G   0.06181   0.02089  0.001228       122       512:   6%|6         | 5/80 [00:03<00:43,  1.71it/s]
      3/49     9.19G   0.06181   0.02089  0.001228       122       512:   8%|7         | 6/80 [00:03<00:41,  1.78it/s]
      3/49     9.19G   0.06165   0.02101  0.001237       139       512:   8%|7         | 6/80 [00:03<00:41,  1.78it/s]
      3/49     9.19G   0.06165   0.02101  0.001237       139       512:   9%|8         | 7/80 [00:03<00:39,  1.83it/s]
      3/49     9.19G   0.06156   0.02101  0.001234       132       512:   9%|8         | 7/80 [00:04<00:39,  1.83it/s]
      3/49     9.19G   0.06156   0.02101  0.001234       132       512:  10%|#         | 8/80 [00:04<00:38,  1.85it/s]
      3/49     9.19G   0.06173   0.02117  0.001228       145       512:  10%|#         | 8/80 [00:04<00:38,  1.85it/s]
      3/49     9.19G   0.06173   0.02117  0.001

      4/49     9.19G   0.06017   0.02069  0.001068       151       512:  25%|##5       | 20/80 [00:10<00:31,  1.88it/s]
      4/49     9.19G   0.06041   0.02061  0.001067       132       512:  25%|##5       | 20/80 [00:11<00:31,  1.88it/s]
      4/49     9.19G   0.06041   0.02061  0.001067       132       512:  26%|##6       | 21/80 [00:11<00:31,  1.90it/s]
      4/49     9.19G   0.06034   0.02058  0.001073       127       512:  26%|##6       | 21/80 [00:11<00:31,  1.90it/s]
      4/49     9.19G   0.06034   0.02058  0.001073       127       512:  28%|##7       | 22/80 [00:11<00:30,  1.91it/s]
      4/49     9.19G    0.0603   0.02081   0.00107       166       512:  28%|##7       | 22/80 [00:12<00:30,  1.91it/s]
      4/49     9.19G    0.0603   0.02081   0.00107       166       512:  29%|##8       | 23/80 [00:12<00:29,  1.91it/s]
      4/49     9.19G   0.06025   0.02091  0.001068       154       512:  29%|##8       | 23/80 [00:12<00:29,  1.91it/s]
      4/49     9.19G   0.06025   0.02091

```
--weights {MODEL_PATH} \ # path to the best model.
--source {TEST_PATH} \ # absolute path to the test images.
--img {IMG_SIZE} \ # Size of image
--conf 0.281 \ # Confidence threshold (default is 0.25)
--iou-thres 0.5 \ # IOU threshold (default is 0.45)
--max-det 3 \ # Number of detections per image (default is 1000) 
--save-txt \ # Save predicted bounding box coordinates as txt files
--save-conf # Save the confidence of prediction for each bounding box
```

In [12]:
!python detect.py --weights {MODEL_PATH} \
                  --source {TEST_PATH} \
                  --img {IMG_SIZE} \
                  --conf 0.25 \
                  --iou-thres 0.5 \
                  --max-det 3 \
                  --save-txt \
                  --save-conf \
                  --visualize


      5/49     9.19G   0.05955   0.02034  0.000969       142       512:  52%|#####2    | 42/80 [00:22<00:19,  1.90it/s]
      5/49     9.19G   0.05961   0.02036 0.0009707       148       512:  52%|#####2    | 42/80 [00:22<00:19,  1.90it/s]
      5/49     9.19G   0.05961   0.02036 0.0009707       148       512:  54%|#####3    | 43/80 [00:22<00:19,  1.89it/s]
      5/49     9.19G   0.05955   0.02044 0.0009714       159       512:  54%|#####3    | 43/80 [00:23<00:19,  1.89it/s]
      5/49     9.19G   0.05955   0.02044 0.0009714       159       512:  55%|#####5    | 44/80 [00:23<00:18,  1.90it/s]
      5/49     9.19G   0.05944   0.02043 0.0009716       132       512:  55%|#####5    | 44/80 [00:23<00:18,  1.90it/s]
      5/49     9.19G   0.05944   0.02043 0.0009716       132       512:  56%|#####6    | 45/80 [00:23<00:18,  1.91it/s]
      5/49     9.19G   0.05939   0.02043 0.0009703       140       512:  56%|#####6    | 45/80 [00:24<00:18,  1.91it/s]
      5/49     9.19G   0.05939   0.0204

      6/49     9.19G   0.05818   0.02085 0.0008582       141       512:  25%|##5       | 20/80 [00:10<00:31,  1.93it/s]
      6/49     9.19G   0.05818   0.02085 0.0008582       141       512:  26%|##6       | 21/80 [00:10<00:30,  1.94it/s]
      6/49     9.19G   0.05799   0.02083 0.0008559       135       512:  26%|##6       | 21/80 [00:11<00:30,  1.94it/s]
      6/49     9.19G   0.05799   0.02083 0.0008559       135       512:  28%|##7       | 22/80 [00:11<00:29,  1.93it/s]
      6/49     9.19G   0.05808   0.02069 0.0008548       112       512:  28%|##7       | 22/80 [00:11<00:29,  1.93it/s]
      6/49     9.19G   0.05808   0.02069 0.0008548       112       512:  29%|##8       | 23/80 [00:11<00:29,  1.93it/s]
      6/49     9.19G   0.05789   0.02067 0.0008562       130       512:  29%|##8       | 23/80 [00:12<00:29,  1.93it/s]
      6/49     9.19G   0.05789   0.02067 0.0008562       130       512:  30%|###       | 24/80 [00:12<00:28,  1.94it/s]
      6/49     9.19G   0.05797    0.0206

     14/49     9.19G   0.05371   0.02064 0.0004793       144       512:  15%|#5        | 12/80 [00:06<00:36,  1.87it/s]
     14/49     9.19G   0.05371   0.02064 0.0004793       144       512:  16%|#6        | 13/80 [00:06<00:36,  1.82it/s]
     14/49     9.19G   0.05356   0.02049 0.0004788       127       512:  16%|#6        | 13/80 [00:07<00:36,  1.82it/s]
     14/49     9.19G   0.05356   0.02049 0.0004788       127       512:  18%|#7        | 14/80 [00:07<00:36,  1.79it/s]
     14/49     9.19G   0.05345   0.02043 0.0004812       132       512:  18%|#7        | 14/80 [00:08<00:36,  1.79it/s]
     14/49     9.19G   0.05345   0.02043 0.0004812       132       512:  19%|#8        | 15/80 [00:08<00:36,  1.80it/s]
     14/49     9.19G   0.05349   0.02051 0.0004821       155       512:  19%|#8        | 15/80 [00:08<00:36,  1.80it/s]
     14/49     9.19G   0.05349   0.02051 0.0004821       155       512:  20%|##        | 16/80 [00:08<00:35,  1.82it/s]
     14/49     9.19G   0.05326   0.02033

     19/49     9.19G    0.0524   0.01962 0.0003635       124       512:  31%|###1      | 25/80 [00:13<00:28,  1.91it/s]
     19/49     9.19G    0.0524   0.01962 0.0003635       124       512:  32%|###2      | 26/80 [00:13<00:28,  1.92it/s]
     19/49     9.19G   0.05246   0.01968 0.0003625       148       512:  32%|###2      | 26/80 [00:14<00:28,  1.92it/s]
     19/49     9.19G   0.05246   0.01968 0.0003625       148       512:  34%|###3      | 27/80 [00:14<00:27,  1.92it/s]
     19/49     9.19G   0.05245   0.01959 0.0003632       123       512:  34%|###3      | 27/80 [00:14<00:27,  1.92it/s]
     19/49     9.19G   0.05245   0.01959 0.0003632       123       512:  35%|###5      | 28/80 [00:14<00:27,  1.90it/s]
     19/49     9.19G   0.05249   0.01958 0.0003633       131       512:  35%|###5      | 28/80 [00:15<00:27,  1.90it/s]
     19/49     9.19G   0.05249   0.01958 0.0003633       131       512:  36%|###6      | 29/80 [00:15<00:27,  1.88it/s]
     19/49     9.19G   0.05245   0.01969

     20/49     9.19G   0.05136    0.0202 0.0003247       137       512:  22%|##2       | 18/80 [00:09<00:32,  1.93it/s]
     20/49     9.19G   0.05136    0.0202 0.0003247       137       512:  24%|##3       | 19/80 [00:09<00:31,  1.93it/s]
     20/49     9.19G   0.05143   0.02006 0.0003252       122       512:  24%|##3       | 19/80 [00:10<00:31,  1.93it/s]
     20/49     9.19G   0.05143   0.02006 0.0003252       122       512:  25%|##5       | 20/80 [00:10<00:31,  1.93it/s]
     20/49     9.19G   0.05145   0.02005 0.0003246       136       512:  25%|##5       | 20/80 [00:11<00:31,  1.93it/s]
     20/49     9.19G   0.05145   0.02005 0.0003246       136       512:  26%|##6       | 21/80 [00:11<00:30,  1.93it/s]
     20/49     9.19G   0.05153   0.02001 0.0003235       131       512:  26%|##6       | 21/80 [00:11<00:30,  1.93it/s]
     20/49     9.19G   0.05153   0.02001 0.0003235       131       512:  28%|##7       | 22/80 [00:11<00:29,  1.94it/s]
     20/49     9.19G   0.05158   0.01984

...

YOLOv5  v5.0-350-gf409d8e torch 1.8.1 CUDA:0 (NVIDIA GeForce GTX 1080 Ti, 11264.0MB)

Fusing layers... 
Model Summary: 224 layers, 7056607 parameters, 0 gradients, 16.3 GFLOPs
D:\Datasets\SIIM_RSNA_Covid_Datasets\tmp\yolov5\utils\plots.py:424: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  fig, ax = plt.subplots(math.ceil(n / 8), 8, tight_layout=True)  # 8 rows x n/8 cols


Saving runs\detect\exp4\01f948f8e544\stage21_Conv_features.png... (32/256)
Saving runs\detect\exp4\01f948f8e544\stage22_Concat_features.png... (32/512)
Saving runs\detect\exp4\01f948f8e544\stage23_C3_features.png... (32/512)
512x512 Done. (21.960s)
image 5/180 D:\Datasets\SIIM_RSNA_Covid_Datasets\test_jpeg_512\022146012034.jpg: Saving runs\detect\exp4\022146012034\stage0_Focus_features.png... (32/32)
Saving runs\detect\exp4\022146012034\stage1_Conv_features.png... (32/64)
Saving runs\detect\exp4\022146012034\stage2_C3_features.png... (32/64)
Saving runs\detect\exp4\022146012034\stage3_Conv_features.png... (32/128)
Saving runs\detect\exp4\022146012034\stage4_C3_features.png... (32/128)
Saving runs\detect\exp4\022146012034\stage5_Conv_features.png... (32/256)
Saving runs\detect\exp4\022146012034\stage6_C3_features.png... (32/256)
Saving runs\detect\exp4\022146012034\stage7_Conv_features.png... (32/512)
Saving runs\detect\exp4\022146012034\stage8_SPP_features.png... (32/512)
Saving runs\d

Saving runs\detect\exp4\047ba804182b\stage4_C3_features.png... (32/128)
Saving runs\detect\exp4\047ba804182b\stage5_Conv_features.png... (32/256)
Saving runs\detect\exp4\047ba804182b\stage6_C3_features.png... (32/256)
Saving runs\detect\exp4\047ba804182b\stage7_Conv_features.png... (32/512)
Saving runs\detect\exp4\047ba804182b\stage8_SPP_features.png... (32/512)
Saving runs\detect\exp4\047ba804182b\stage9_C3_features.png... (32/512)
Saving runs\detect\exp4\047ba804182b\stage10_Conv_features.png... (32/256)
Saving runs\detect\exp4\047ba804182b\stage11_Upsample_features.png... (32/256)
Saving runs\detect\exp4\047ba804182b\stage12_Concat_features.png... (32/512)
Saving runs\detect\exp4\047ba804182b\stage13_C3_features.png... (32/256)
Saving runs\detect\exp4\047ba804182b\stage14_Conv_features.png... (32/128)
Saving runs\detect\exp4\047ba804182b\stage15_Upsample_features.png... (32/128)
Saving runs\detect\exp4\047ba804182b\stage16_Concat_features.png... (32/256)
Saving runs\detect\exp4\047b

Saving runs\detect\exp4\1a4c378605f5\stage14_Conv_features.png... (32/128)
Saving runs\detect\exp4\1a4c378605f5\stage15_Upsample_features.png... (32/128)
Saving runs\detect\exp4\1a4c378605f5\stage16_Concat_features.png... (32/256)
Saving runs\detect\exp4\1a4c378605f5\stage17_C3_features.png... (32/128)
Saving runs\detect\exp4\1a4c378605f5\stage18_Conv_features.png... (32/128)
Saving runs\detect\exp4\1a4c378605f5\stage19_Concat_features.png... (32/256)
Saving runs\detect\exp4\1a4c378605f5\stage20_C3_features.png... (32/256)
Saving runs\detect\exp4\1a4c378605f5\stage21_Conv_features.png... (32/256)
Saving runs\detect\exp4\1a4c378605f5\stage22_Concat_features.png... (32/512)
Saving runs\detect\exp4\1a4c378605f5\stage23_C3_features.png... (32/512)
512x512 Done. (19.805s)
image 133/180 D:\Datasets\SIIM_RSNA_Covid_Datasets\test_jpeg_512\1aa1491c9cd1.jpg: Saving runs\detect\exp4\1aa1491c9cd1\stage0_Focus_features.png... (32/32)
Saving runs\detect\exp4\1aa1491c9cd1\stage1_Conv_features.png... 

Saving runs\detect\exp4\1c5aa8c405c7\stage19_Concat_features.png... (32/256)
Saving runs\detect\exp4\1c5aa8c405c7\stage20_C3_features.png... (32/256)
Saving runs\detect\exp4\1c5aa8c405c7\stage21_Conv_features.png... (32/256)
Saving runs\detect\exp4\1c5aa8c405c7\stage22_Concat_features.png... (32/512)
Saving runs\detect\exp4\1c5aa8c405c7\stage23_C3_features.png... (32/512)
512x512 Done. (20.875s)
image 149/180 D:\Datasets\SIIM_RSNA_Covid_Datasets\test_jpeg_512\1c69c1af9a67.jpg: Saving runs\detect\exp4\1c69c1af9a67\stage0_Focus_features.png... (32/32)
Saving runs\detect\exp4\1c69c1af9a67\stage1_Conv_features.png... (32/64)
Saving runs\detect\exp4\1c69c1af9a67\stage2_C3_features.png... (32/64)
Saving runs\detect\exp4\1c69c1af9a67\stage3_Conv_features.png... (32/128)
Saving runs\detect\exp4\1c69c1af9a67\stage4_C3_features.png... (32/128)
Saving runs\detect\exp4\1c69c1af9a67\stage5_Conv_features.png... (32/256)
Saving runs\detect\exp4\1c69c1af9a67\stage6_C3_features.png... (32/256)
Saving r

#### Run 4 Inference

In [14]:
# absolute path
TEST_PATH = 'D:\\Datasets\\SIIM_RSNA_Covid_Datasets\\test_jpeg_512'
MODEL_PATH = 'SIIM_COVID_512_Runs/exp5/weights/best.pt'

!python detect.py --weights {MODEL_PATH} \
                  --source {TEST_PATH} \
                  --img {IMG_SIZE} \
                  --conf 0.25 \
                  --iou-thres 0.5 \
                  --max-det 3 \
                  --save-txt \
                  --save-conf \
                  --visualize

      1/49     9.19G    0.0697   0.02255  0.002379       149       512:  18%|#7        | 14/80 [00:08<00:36,  1.82it/s]
      1/49     9.19G    0.0697   0.02255  0.002379       149       512:  19%|#8        | 15/80 [00:08<00:34,  1.87it/s]
      1/49     9.19G   0.06934   0.02284  0.002389       164       512:  19%|#8        | 15/80 [00:08<00:34,  1.87it/s]
      1/49     9.19G   0.06934   0.02284  0.002389       164       512:  20%|##        | 16/80 [00:08<00:33,  1.90it/s]
      1/49     9.19G   0.06909   0.02291  0.002373       144       512:  20%|##        | 16/80 [00:09<00:33,  1.90it/s]
      1/49     9.19G   0.06909   0.02291  0.002373       144       512:  21%|##1       | 17/80 [00:09<00:32,  1.92it/s]
      1/49     9.19G   0.06896   0.02288  0.002356       134       512:  21%|##1       | 17/80 [00:09<00:32,  1.92it/s]
      1/49     9.19G   0.06896   0.02288  0.002356       134       512:  22%|##2       | 18/80 [00:09<00:32,  1.93it/s]
      1/49     9.19G   0.06895   0.02285

               Class     Images     Labels          P          R     mAP@.5 mAP@.5:.95:  50%|#####     | 5/10 [00:03<00:03,  1.49it/s]
               Class     Images     Labels          P          R     mAP@.5 mAP@.5:.95:  60%|######    | 6/10 [00:04<00:02,  1.48it/s]
               Class     Images     Labels          P          R     mAP@.5 mAP@.5:.95:  70%|#######   | 7/10 [00:04<00:02,  1.49it/s]
               Class     Images     Labels          P          R     mAP@.5 mAP@.5:.95:  80%|########  | 8/10 [00:05<00:01,  1.48it/s]
               Class     Images     Labels          P          R     mAP@.5 mAP@.5:.95:  90%|######### | 9/10 [00:06<00:00,  1.50it/s]
               Class     Images     Labels          P          R     mAP@.5 mAP@.5:.95: 100%|##########| 10/10 [00:06<00:00,  1.56it/s]
               Class     Images     Labels          P          R     mAP@.5 mAP@.5:.95: 100%|##########| 10/10 [00:06<00:00,  1.51it/s]

     Epoch   gpu_mem       box       obj       cls  

     14/49     9.19G   0.05629   0.02065 0.0006745       137       512:  34%|###3      | 27/80 [00:14<00:27,  1.94it/s]
     14/49     9.19G   0.05629   0.02067 0.0006732       147       512:  34%|###3      | 27/80 [00:14<00:27,  1.94it/s]
     14/49     9.19G   0.05629   0.02067 0.0006732       147       512:  35%|###5      | 28/80 [00:14<00:26,  1.94it/s]
     14/49     9.19G   0.05622   0.02063 0.0006731       124       512:  35%|###5      | 28/80 [00:15<00:26,  1.94it/s]
     14/49     9.19G   0.05622   0.02063 0.0006731       124       512:  36%|###6      | 29/80 [00:15<00:26,  1.94it/s]
     14/49     9.19G   0.05629   0.02061 0.0006759       132       512:  36%|###6      | 29/80 [00:15<00:26,  1.94it/s]
     14/49     9.19G   0.05629   0.02061 0.0006759       132       512:  38%|###7      | 30/80 [00:15<00:25,  1.93it/s]
     14/49     9.19G   0.05622   0.02057  0.000676       132       512:  38%|###7      | 30/80 [00:16<00:25,  1.93it/s]
     14/49     9.19G   0.05622   0.02057

     15/49     9.19G    0.0559   0.02056 0.0006133       127       512:  51%|#####1    | 41/80 [00:21<00:20,  1.87it/s]
     15/49     9.19G   0.05588   0.02056  0.000612       137       512:  51%|#####1    | 41/80 [00:21<00:20,  1.87it/s]
     15/49     9.19G   0.05588   0.02056  0.000612       137       512:  52%|#####2    | 42/80 [00:21<00:20,  1.87it/s]
     15/49     9.19G   0.05588   0.02052 0.0006111       122       512:  52%|#####2    | 42/80 [00:22<00:20,  1.87it/s]
     15/49     9.19G   0.05588   0.02052 0.0006111       122       512:  54%|#####3    | 43/80 [00:22<00:19,  1.87it/s]
     15/49     9.19G   0.05596   0.02055 0.0006117       145       512:  54%|#####3    | 43/80 [00:22<00:19,  1.87it/s]
     15/49     9.19G   0.05596   0.02055 0.0006117       145       512:  55%|#####5    | 44/80 [00:23<00:19,  1.84it/s]
     15/49     9.19G   0.05598   0.02051  0.000614       128       512:  55%|#####5    | 44/80 [00:23<00:19,  1.84it/s]
     15/49     9.19G   0.05598   0.02051

     17/49     9.19G   0.05614   0.01988 0.0005868       133       512:  35%|###5      | 28/80 [00:14<00:26,  1.93it/s]
     17/49     9.19G     0.056   0.01992 0.0005884       143       512:  35%|###5      | 28/80 [00:15<00:26,  1.93it/s]
     17/49     9.19G     0.056   0.01992 0.0005884       143       512:  36%|###6      | 29/80 [00:15<00:26,  1.93it/s]
     17/49     9.19G   0.05591   0.02003 0.0005867       149       512:  36%|###6      | 29/80 [00:15<00:26,  1.93it/s]
     17/49     9.19G   0.05591   0.02003 0.0005867       149       512:  38%|###7      | 30/80 [00:15<00:26,  1.90it/s]
     17/49     9.19G   0.05603   0.01999 0.0005862       129       512:  38%|###7      | 30/80 [00:16<00:26,  1.90it/s]
     17/49     9.19G   0.05603   0.01999 0.0005862       129       512:  39%|###8      | 31/80 [00:16<00:25,  1.90it/s]
     17/49     9.19G   0.05603   0.01997 0.0005864       133       512:  39%|###8      | 31/80 [00:16<00:25,  1.90it/s]
     17/49     9.19G   0.05603   0.01997

...


Saving runs\detect\exp5\042979d394a1\stage6_C3_features.png... (32/256)
Saving runs\detect\exp5\042979d394a1\stage7_Conv_features.png... (32/512)
Saving runs\detect\exp5\042979d394a1\stage8_SPP_features.png... (32/512)
Saving runs\detect\exp5\042979d394a1\stage9_C3_features.png... (32/512)
Saving runs\detect\exp5\042979d394a1\stage10_Conv_features.png... (32/256)
Saving runs\detect\exp5\042979d394a1\stage11_Upsample_features.png... (32/256)
Saving runs\detect\exp5\042979d394a1\stage12_Concat_features.png... (32/512)
Saving runs\detect\exp5\042979d394a1\stage13_C3_features.png... (32/256)
Saving runs\detect\exp5\042979d394a1\stage14_Conv_features.png... (32/128)
Saving runs\detect\exp5\042979d394a1\stage15_Upsample_features.png... (32/128)
Saving runs\detect\exp5\042979d394a1\stage16_Concat_features.png... (32/256)
Saving runs\detect\exp5\042979d394a1\stage17_C3_features.png... (32/128)
Saving runs\detect\exp5\042979d394a1\stage18_Conv_features.png... (32/128)
Saving runs\detect\exp5\0

Saving runs\detect\exp5\05435da60872\stage23_C3_features.png... (32/512)
512x512 2 opacitys, Done. (18.583s)
image 22/180 D:\Datasets\SIIM_RSNA_Covid_Datasets\test_jpeg_512\0562436fde50.jpg: Saving runs\detect\exp5\0562436fde50\stage0_Focus_features.png... (32/32)
Saving runs\detect\exp5\0562436fde50\stage1_Conv_features.png... (32/64)
Saving runs\detect\exp5\0562436fde50\stage2_C3_features.png... (32/64)
Saving runs\detect\exp5\0562436fde50\stage3_Conv_features.png... (32/128)
Saving runs\detect\exp5\0562436fde50\stage4_C3_features.png... (32/128)
Saving runs\detect\exp5\0562436fde50\stage5_Conv_features.png... (32/256)
Saving runs\detect\exp5\0562436fde50\stage6_C3_features.png... (32/256)
Saving runs\detect\exp5\0562436fde50\stage7_Conv_features.png... (32/512)
Saving runs\detect\exp5\0562436fde50\stage8_SPP_features.png... (32/512)
Saving runs\detect\exp5\0562436fde50\stage9_C3_features.png... (32/512)
Saving runs\detect\exp5\0562436fde50\stage10_Conv_features.png... (32/256)
Savin

Saving runs\detect\exp5\18e043b70fda\stage19_Concat_features.png... (32/256)
Saving runs\detect\exp5\18e043b70fda\stage20_C3_features.png... (32/256)
Saving runs\detect\exp5\18e043b70fda\stage21_Conv_features.png... (32/256)
Saving runs\detect\exp5\18e043b70fda\stage22_Concat_features.png... (32/512)
Saving runs\detect\exp5\18e043b70fda\stage23_C3_features.png... (32/512)
512x512 Done. (19.801s)
image 126/180 D:\Datasets\SIIM_RSNA_Covid_Datasets\test_jpeg_512\18e6a4083920.jpg: Saving runs\detect\exp5\18e6a4083920\stage0_Focus_features.png... (32/32)
Saving runs\detect\exp5\18e6a4083920\stage1_Conv_features.png... (32/64)
Saving runs\detect\exp5\18e6a4083920\stage2_C3_features.png... (32/64)
Saving runs\detect\exp5\18e6a4083920\stage3_Conv_features.png... (32/128)
Saving runs\detect\exp5\18e6a4083920\stage4_C3_features.png... (32/128)
Saving runs\detect\exp5\18e6a4083920\stage5_Conv_features.png... (32/256)
Saving runs\detect\exp5\18e6a4083920\stage6_C3_features.png... (32/256)
Saving r

Saving runs\detect\exp5\1c1c48cb66e4\stage13_C3_features.png... (32/256)
Saving runs\detect\exp5\1c1c48cb66e4\stage14_Conv_features.png... (32/128)
Saving runs\detect\exp5\1c1c48cb66e4\stage15_Upsample_features.png... (32/128)
Saving runs\detect\exp5\1c1c48cb66e4\stage16_Concat_features.png... (32/256)
Saving runs\detect\exp5\1c1c48cb66e4\stage17_C3_features.png... (32/128)
Saving runs\detect\exp5\1c1c48cb66e4\stage18_Conv_features.png... (32/128)
Saving runs\detect\exp5\1c1c48cb66e4\stage19_Concat_features.png... (32/256)
Saving runs\detect\exp5\1c1c48cb66e4\stage20_C3_features.png... (32/256)
Saving runs\detect\exp5\1c1c48cb66e4\stage21_Conv_features.png... (32/256)
Saving runs\detect\exp5\1c1c48cb66e4\stage22_Concat_features.png... (32/512)
Saving runs\detect\exp5\1c1c48cb66e4\stage23_C3_features.png... (32/512)
512x512 Done. (20.194s)
image 146/180 D:\Datasets\SIIM_RSNA_Covid_Datasets\test_jpeg_512\1c1e9d3f5bab.jpg: Saving runs\detect\exp5\1c1e9d3f5bab\stage0_Focus_features.png... 

Saving runs\detect\exp5\1d9a8f9f0eef\stage20_C3_features.png... (32/256)
Saving runs\detect\exp5\1d9a8f9f0eef\stage21_Conv_features.png... (32/256)
Saving runs\detect\exp5\1d9a8f9f0eef\stage22_Concat_features.png... (32/512)
Saving runs\detect\exp5\1d9a8f9f0eef\stage23_C3_features.png... (32/512)
512x512 2 opacitys, Done. (20.705s)
image 158/180 D:\Datasets\SIIM_RSNA_Covid_Datasets\test_jpeg_512\1dccbb75ffba.jpg: Saving runs\detect\exp5\1dccbb75ffba\stage0_Focus_features.png... (32/32)
Saving runs\detect\exp5\1dccbb75ffba\stage1_Conv_features.png... (32/64)
Saving runs\detect\exp5\1dccbb75ffba\stage2_C3_features.png... (32/64)
Saving runs\detect\exp5\1dccbb75ffba\stage3_Conv_features.png... (32/128)
Saving runs\detect\exp5\1dccbb75ffba\stage4_C3_features.png... (32/128)
Saving runs\detect\exp5\1dccbb75ffba\stage5_Conv_features.png... (32/256)
Saving runs\detect\exp5\1dccbb75ffba\stage6_C3_features.png... (32/256)
Saving runs\detect\exp5\1dccbb75ffba\stage7_Conv_features.png... (32/512)

#### Run 5 Inference

In [16]:
# absolute path
TEST_PATH = 'D:\\Datasets\\SIIM_RSNA_Covid_Datasets\\test_jpeg_512'
MODEL_PATH = 'SIIM_COVID_512_Runs/exp6/weights/best.pt'

!python detect.py --weights {MODEL_PATH} \
                  --source {TEST_PATH} \
                  --img {IMG_SIZE} \
                  --conf 0.25 \
                  --iou-thres 0.5 \
                  --max-det 3 \
                  --save-txt \
                  --save-conf \
                  --visualize

      1/49     9.19G   0.08473   0.02421   0.01301       132       512:  10%|#         | 8/80 [00:04<00:36,  1.97it/s]
      1/49     9.19G   0.08455   0.02458   0.01294       156       512:  10%|#         | 8/80 [00:04<00:36,  1.97it/s]
      1/49     9.19G   0.08455   0.02458   0.01294       156       512:  11%|#1        | 9/80 [00:04<00:36,  1.97it/s]
      1/49     9.19G   0.08448   0.02475   0.01282       145       512:  11%|#1        | 9/80 [00:05<00:36,  1.97it/s]
      1/49     9.19G   0.08448   0.02475   0.01282       145       512:  12%|#2        | 10/80 [00:05<00:35,  1.97it/s]
      1/49     9.19G   0.08414    0.0249   0.01275       143       512:  12%|#2        | 10/80 [00:05<00:35,  1.97it/s]
      1/49     9.19G   0.08414    0.0249   0.01275       143       512:  14%|#3        | 11/80 [00:05<00:35,  1.97it/s]
      1/49     9.19G   0.08413    0.0249   0.01266       140       512:  14%|#3        | 11/80 [00:06<00:35,  1.97it/s]
      1/49     9.19G   0.08413    0.0249   0

      2/49     9.19G   0.06894   0.02511  0.004063       143       512:  59%|#####8    | 47/80 [00:26<00:18,  1.77it/s]
      2/49     9.19G   0.06894   0.02511  0.004063       143       512:  60%|######    | 48/80 [00:26<00:17,  1.80it/s]
      2/49     9.19G   0.06888   0.02512  0.004045       145       512:  60%|######    | 48/80 [00:26<00:17,  1.80it/s]
      2/49     9.19G   0.06888   0.02512  0.004045       145       512:  61%|######1   | 49/80 [00:26<00:17,  1.76it/s]
      2/49     9.19G   0.06886   0.02505  0.004027       112       512:  61%|######1   | 49/80 [00:27<00:17,  1.76it/s]
      2/49     9.19G   0.06886   0.02505  0.004027       112       512:  62%|######2   | 50/80 [00:27<00:16,  1.78it/s]
      2/49     9.19G   0.06882   0.02511  0.004016       160       512:  62%|######2   | 50/80 [00:27<00:16,  1.78it/s]
      2/49     9.19G   0.06882   0.02511  0.004016       160       512:  64%|######3   | 51/80 [00:27<00:16,  1.81it/s]
      2/49     9.19G   0.06874   0.02514

     15/49     9.19G   0.05414   0.02025 0.0005745       122       512:  82%|########2 | 66/80 [00:34<00:07,  1.94it/s]
     15/49     9.19G   0.05409   0.02022 0.0005747       125       512:  82%|########2 | 66/80 [00:35<00:07,  1.94it/s]
     15/49     9.19G   0.05409   0.02022 0.0005747       125       512:  84%|########3 | 67/80 [00:35<00:06,  1.94it/s]
     15/49     9.19G   0.05408   0.02023 0.0005743       138       512:  84%|########3 | 67/80 [00:35<00:06,  1.94it/s]
     15/49     9.19G   0.05408   0.02023 0.0005743       138       512:  85%|########5 | 68/80 [00:35<00:06,  1.92it/s]
     15/49     9.19G   0.05405   0.02021 0.0005745       136       512:  85%|########5 | 68/80 [00:36<00:06,  1.92it/s]
     15/49     9.19G   0.05405   0.02021 0.0005745       136       512:  86%|########6 | 69/80 [00:36<00:05,  1.89it/s]
     15/49     9.19G   0.05407   0.02025 0.0005742       155       512:  86%|########6 | 69/80 [00:36<00:05,  1.89it/s]
     15/49     9.19G   0.05407   0.02025

     18/49     9.19G   0.05301   0.01963 0.0004564       135       512:  70%|#######   | 56/80 [00:30<00:12,  1.90it/s]
     18/49     9.19G   0.05301   0.01963 0.0004564       135       512:  71%|#######1  | 57/80 [00:30<00:12,  1.91it/s]
     18/49     9.19G   0.05298   0.01961 0.0004565       130       512:  71%|#######1  | 57/80 [00:30<00:12,  1.91it/s]
     18/49     9.19G   0.05298   0.01961 0.0004565       130       512:  72%|#######2  | 58/80 [00:30<00:11,  1.92it/s]
     18/49     9.19G   0.05305   0.01959 0.0004567       127       512:  72%|#######2  | 58/80 [00:31<00:11,  1.92it/s]
     18/49     9.19G   0.05305   0.01959 0.0004567       127       512:  74%|#######3  | 59/80 [00:31<00:10,  1.93it/s]
     18/49     9.19G   0.05299   0.01955 0.0004565       114       512:  74%|#######3  | 59/80 [00:31<00:10,  1.93it/s]
     18/49     9.19G   0.05299   0.01955 0.0004565       114       512:  75%|#######5  | 60/80 [00:31<00:10,  1.93it/s]
     18/49     9.19G   0.05299    0.0195

     19/49     9.19G   0.05335   0.01994 0.0004273       140       512:  38%|###7      | 30/80 [00:16<00:26,  1.88it/s]
     19/49     9.19G   0.05335   0.01994 0.0004273       140       512:  39%|###8      | 31/80 [00:16<00:26,  1.88it/s]
     19/49     9.19G   0.05328   0.01992 0.0004262       131       512:  39%|###8      | 31/80 [00:16<00:26,  1.88it/s]
     19/49     9.19G   0.05328   0.01992 0.0004262       131       512:  40%|####      | 32/80 [00:16<00:25,  1.90it/s]
     19/49     9.19G   0.05327   0.01999 0.0004258       160       512:  40%|####      | 32/80 [00:17<00:25,  1.90it/s]
     19/49     9.19G   0.05327   0.01999 0.0004258       160       512:  41%|####1     | 33/80 [00:17<00:24,  1.91it/s]
     19/49     9.19G   0.05327   0.02001 0.0004245       143       512:  41%|####1     | 33/80 [00:17<00:24,  1.91it/s]
     19/49     9.19G   0.05327   0.02001 0.0004245       143       512:  42%|####2     | 34/80 [00:17<00:23,  1.92it/s]
     19/49     9.19G   0.05327   0.01994

...


Saving runs\detect\exp6\03fa9d7e94a8\stage9_C3_features.png... (32/512)
Saving runs\detect\exp6\03fa9d7e94a8\stage10_Conv_features.png... (32/256)
Saving runs\detect\exp6\03fa9d7e94a8\stage11_Upsample_features.png... (32/256)
Saving runs\detect\exp6\03fa9d7e94a8\stage12_Concat_features.png... (32/512)
Saving runs\detect\exp6\03fa9d7e94a8\stage13_C3_features.png... (32/256)
Saving runs\detect\exp6\03fa9d7e94a8\stage14_Conv_features.png... (32/128)
Saving runs\detect\exp6\03fa9d7e94a8\stage15_Upsample_features.png... (32/128)
Saving runs\detect\exp6\03fa9d7e94a8\stage16_Concat_features.png... (32/256)
Saving runs\detect\exp6\03fa9d7e94a8\stage17_C3_features.png... (32/128)
Saving runs\detect\exp6\03fa9d7e94a8\stage18_Conv_features.png... (32/128)
Saving runs\detect\exp6\03fa9d7e94a8\stage19_Concat_features.png... (32/256)
Saving runs\detect\exp6\03fa9d7e94a8\stage20_C3_features.png... (32/256)
Saving runs\detect\exp6\03fa9d7e94a8\stage21_Conv_features.png... (32/256)
Saving runs\detect\

Saving runs\detect\exp6\04a083828fec\stage11_Upsample_features.png... (32/256)
Saving runs\detect\exp6\04a083828fec\stage12_Concat_features.png... (32/512)
Saving runs\detect\exp6\04a083828fec\stage13_C3_features.png... (32/256)
Saving runs\detect\exp6\04a083828fec\stage14_Conv_features.png... (32/128)
Saving runs\detect\exp6\04a083828fec\stage15_Upsample_features.png... (32/128)
Saving runs\detect\exp6\04a083828fec\stage16_Concat_features.png... (32/256)
Saving runs\detect\exp6\04a083828fec\stage17_C3_features.png... (32/128)
Saving runs\detect\exp6\04a083828fec\stage18_Conv_features.png... (32/128)
Saving runs\detect\exp6\04a083828fec\stage19_Concat_features.png... (32/256)
Saving runs\detect\exp6\04a083828fec\stage20_C3_features.png... (32/256)
Saving runs\detect\exp6\04a083828fec\stage21_Conv_features.png... (32/256)
Saving runs\detect\exp6\04a083828fec\stage22_Concat_features.png... (32/512)
Saving runs\detect\exp6\04a083828fec\stage23_C3_features.png... (32/512)
512x512 1 opacity

Saving runs\detect\exp6\181a2a300bb8\stage17_C3_features.png... (32/128)
Saving runs\detect\exp6\181a2a300bb8\stage18_Conv_features.png... (32/128)
Saving runs\detect\exp6\181a2a300bb8\stage19_Concat_features.png... (32/256)
Saving runs\detect\exp6\181a2a300bb8\stage20_C3_features.png... (32/256)
Saving runs\detect\exp6\181a2a300bb8\stage21_Conv_features.png... (32/256)
Saving runs\detect\exp6\181a2a300bb8\stage22_Concat_features.png... (32/512)
Saving runs\detect\exp6\181a2a300bb8\stage23_C3_features.png... (32/512)
512x512 1 opacity, Done. (19.693s)
image 123/180 D:\Datasets\SIIM_RSNA_Covid_Datasets\test_jpeg_512\1863b31637f6.jpg: Saving runs\detect\exp6\1863b31637f6\stage0_Focus_features.png... (32/32)
Saving runs\detect\exp6\1863b31637f6\stage1_Conv_features.png... (32/64)
Saving runs\detect\exp6\1863b31637f6\stage2_C3_features.png... (32/64)
Saving runs\detect\exp6\1863b31637f6\stage3_Conv_features.png... (32/128)
Saving runs\detect\exp6\1863b31637f6\stage4_C3_features.png... (32/

Saving runs\detect\exp6\1b282faf0f42\stage21_Conv_features.png... (32/256)
Saving runs\detect\exp6\1b282faf0f42\stage22_Concat_features.png... (32/512)
Saving runs\detect\exp6\1b282faf0f42\stage23_C3_features.png... (32/512)
512x512 Done. (20.091s)
image 139/180 D:\Datasets\SIIM_RSNA_Covid_Datasets\test_jpeg_512\1b40a20045ee.jpg: Saving runs\detect\exp6\1b40a20045ee\stage0_Focus_features.png... (32/32)
Saving runs\detect\exp6\1b40a20045ee\stage1_Conv_features.png... (32/64)
Saving runs\detect\exp6\1b40a20045ee\stage2_C3_features.png... (32/64)
Saving runs\detect\exp6\1b40a20045ee\stage3_Conv_features.png... (32/128)
Saving runs\detect\exp6\1b40a20045ee\stage4_C3_features.png... (32/128)
Saving runs\detect\exp6\1b40a20045ee\stage5_Conv_features.png... (32/256)
Saving runs\detect\exp6\1b40a20045ee\stage6_C3_features.png... (32/256)
Saving runs\detect\exp6\1b40a20045ee\stage7_Conv_features.png... (32/512)
Saving runs\detect\exp6\1b40a20045ee\stage8_SPP_features.png... (32/512)
Saving runs

image 145/180 D:\Datasets\SIIM_RSNA_Covid_Datasets\test_jpeg_512\1c1c48cb66e4.jpg: Saving runs\detect\exp6\1c1c48cb66e4\stage0_Focus_features.png... (32/32)
Saving runs\detect\exp6\1c1c48cb66e4\stage1_Conv_features.png... (32/64)
Saving runs\detect\exp6\1c1c48cb66e4\stage2_C3_features.png... (32/64)
Saving runs\detect\exp6\1c1c48cb66e4\stage3_Conv_features.png... (32/128)
Saving runs\detect\exp6\1c1c48cb66e4\stage4_C3_features.png... (32/128)
Saving runs\detect\exp6\1c1c48cb66e4\stage5_Conv_features.png... (32/256)
Saving runs\detect\exp6\1c1c48cb66e4\stage6_C3_features.png... (32/256)
Saving runs\detect\exp6\1c1c48cb66e4\stage7_Conv_features.png... (32/512)
Saving runs\detect\exp6\1c1c48cb66e4\stage8_SPP_features.png... (32/512)
Saving runs\detect\exp6\1c1c48cb66e4\stage9_C3_features.png... (32/512)
Saving runs\detect\exp6\1c1c48cb66e4\stage10_Conv_features.png... (32/256)
Saving runs\detect\exp6\1c1c48cb66e4\stage11_Upsample_features.png... (32/256)
Saving runs\detect\exp6\1c1c48cb66